In [ ]:
# ..... get cell types using Mantri et al markers ..... #

In [3]:
library(SingleCellExperiment)
library(MetaMarkers)
library(Seurat)
library(data.table)
library(dplyr)

In [4]:
# load list of orthologs
om = read.delim('turtle_chicken_orthologs_biomart.txt', sep = '\t')
colnames(om) <- c('turtle', 'chicken', 'LCA', 'homology_type', 'orthology_confidence')
om <- om[om[,1]!='' & om[,2]!='' & om$homology_type=='ortholog_one2one',]
dim(om)
om[1,]

[1] 11338     5

turtle chicken LCA           homology_type    orthology_confidence
10 ND2    ND2     Archelosauria ortholog_one2one 1

In [5]:
# list of stages and samples
stages = rep(c('stage14', 'stage17', 'stage21'), each = 3)
samples = paste0('sample', c('4', '7', '8A', '3_Triangle', '5B', '5Y', '1A', '1B', '2'))

In [6]:
# function to get top 100 markers for each cell type
get_top_markers <- function(markers, ctypes){
    markers$rank = NA
    for(ii in 1:length(ctypes)){
        id = which(markers$cell_type==ctypes[ii])
        markers$rank[id] = 1:length(id)
    }
    return(markers)
}

In [7]:
# load markers
markers = fread('~/septation/markers/Mantri/Mantri_celltype_markers.csv.gz')
markers$gene <- om$turtle[match(markers$gene, om$chicken)]
markers <- markers[!is.na(markers$gene),]

markers <- markers[markers$cell_type!='TMSB4X high cells',]
ctypes = unique(markers$cell_type)

# get rank of markers
markers = get_top_markers(markers, ctypes)
markers[1:2,]

# tibble of group, cell_type, gene, rank
top_markers = as_tibble(markers[which(markers$rank<=100),c('group', 'cell_type', 'gene')])
top_markers[1:2,]

group cell_type        gene  fold_change auroc     log_fdr   population_size
1 all   Cardiomyocytes-1 TPM4  3.122102    0.8517201 -1202.058 1873           
2 all   Cardiomyocytes-1 ACTC1 3.023225    0.8459063 -1162.641 1873           
  population_fraction average_expression se_expression detection_rate
1 0.1326863            9733.35           105.4473      0.9951949     
2 0.1326863           17342.16           222.9295      0.9994661     
  fold_change_detection precision recall    rank
1 1.324510              0.1685353 0.9951949 1   
2 1.212354              0.1564825 0.9994661 2

group cell_type        gene 
1 all   Cardiomyocytes-1 TPM4 
2 all   Cardiomyocytes-1 ACTC1

In [9]:
# get cell type anno
pb = txtProgressBar(min = 0, max = length(samples), initial = 0)

for(id in 1:length(samples)){
    
    # load seurat object
    sce = readRDS(paste0(stages[id], '_', samples[id], '_data.rds'))

    # get SCE object
    sc3 = SingleCellExperiment(list(counts = sce@assays$RNA@counts))
    colData(sc3) <- DataFrame(sce@meta.data)
    assay(sc3, "cpm") = convert_to_cpm(assay(sc3))
    
    # predict cell type neighborhood
    ct_scores = score_cells(log1p(cpm(sc3)), top_markers)
    ct_enrichment = compute_marker_enrichment(ct_scores)
    ct_pred = assign_cells(ct_scores)
    
    # save
    write.table(ct_pred, file = paste0('annotations/', stages[id], '_', samples[id], '_Mantri_celltypes.csv'),
            sep = ',', row.names = T, col.names = T, quote = F)
    
    setTxtProgressBar(pb, id)
}